In [1]:
from PIL import Image

image = Image.open("/media/user/9c7eaef1-35fa-4210-889c-9e2b99342586/user/abul/RESM NEW NEW/RESM/20100903_0025_hr_patch_11.jpg")
mode = image.mode
channels = {"L": 1, "RGB": 3, "RGBA": 4, "CMYK": 4}  # Mapping for common modes
num_channels = channels.get(mode, "Unknown")
print(f"Number of channels: {num_channels}")


Number of channels: 1


In [2]:
import os 
import torch.nn as nn
from torchsummary import summary
import torch.optim as optim
from PIL import Image
import torchvision.transforms as transforms
from torch.utils.data import Dataset, random_split
import random


from conv_layer import conv_layer
from RLFB import RLFB
from SUBP import SubPixelConvBlock
from Trainning_Loop import train_model, CharbonnierLoss

/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
class MESR(nn.Module):
    def __init__(self,in_channels,mid_channels,out_channels, num_blocks=12, upscale_factor=4):
        super(MESR, self).__init__()
        self.conv_in = conv_layer(in_channels, mid_channels, 3)
        self.RLFB_blocks = nn.Sequential(*[RLFB(mid_channels) for _ in range(num_blocks)])
        self.conv_out1 = conv_layer(mid_channels, mid_channels, 3)
        self.conv_out2 = conv_layer(mid_channels, out_channels, 3)
        self.sub_pixel_conv = SubPixelConvBlock(out_channels, out_channels, upscale_factor=upscale_factor)
    def forward(self, x):
        out_conv_in = self.conv_in(x)  
        out_RLFB = self.RLFB_blocks(out_conv_in)
        out2_conv_in = self.conv_out1(out_RLFB)  
        out_skip = out2_conv_in + out_conv_in  
        out = self.conv_out2(out_skip)  
        out = self.sub_pixel_conv(out)  
        return out
def model_summary(model, device):
    model.to(device)
    summary(model, input_size=(1, 128, 128)) # Change order & num of channels to match grayscale channel

In [4]:
class SuperResolutionDataset(Dataset):
    def __init__(self, lr_dir, hr_dir, lr_transform=None, hr_transform=None):
        self.lr_dir = lr_dir
        self.hr_dir = hr_dir
        self.lr_images = os.listdir(lr_dir)
        self.lr_transform = lr_transform
        self.hr_transform = hr_transform

    def __len__(self):
        return len(self.lr_images)

    def __getitem__(self, idx):
        lr_image_path = os.path.join(self.lr_dir, self.lr_images[idx])
        hr_image_path = os.path.join(self.hr_dir, self.lr_images[idx])

        lr_image = Image.open(lr_image_path).convert("L")  # Convert to grayscale
        hr_image = Image.open(hr_image_path).convert("L")  # Convert to grayscale

        if self.lr_transform:
            lr_image = self.lr_transform(lr_image)
        if self.hr_transform:
            hr_image = self.hr_transform(hr_image)

        return {'image': lr_image, 'label': hr_image}

In [5]:
def dataloaders(train_dataset, val_dataset, batch_size=32): # setting the batch size to 2
    train_loader = torch.utils.data.DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
    val_loader = torch.utils.data.DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
    return train_loader, val_loader


def setup_training(model, device, train_loader, val_loader, epochs=500, patience=100):
    optimizer = optim.AdamW(model.parameters(), lr=0.001)
    loss_function = CharbonnierLoss(epsilon=1e-6)
    lr_scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer, mode='min', factor=0.1, patience=10, min_lr=1e-6, verbose=True)



    train_model(
        model=model,
        train_loader=train_loader,
        val_loader=val_loader,
        optimizer=optimizer,
        loss_function=loss_function,
        device=device,
        epochs=epochs,
        patience=patience,
        lr_scheduler=lr_scheduler,

        output_dir="model_output"  # Specify the output directory
    )


In [6]:
import torch

# Check if GPU is available
if torch.cuda.is_available():
    device = torch.device("cuda")
    print("GPU is being used. Device:", torch.cuda.get_device_name(0))
else:
    device = torch.device("cpu")
    print("Using CPU instead of GPU.")

GPU is being used. Device: NVIDIA RTX A6000


In [ ]:
def main():
    if torch.cuda.is_available():
        print("CUDA is available!")
        print(f"Number of available GPUs: {torch.cuda.device_count()}")
        print(f"Current device: {torch.cuda.current_device()}")
        print(f"Device name: {torch.cuda.get_device_name(torch.cuda.current_device())}")
    else:
        print("CUDA is not available.")

    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

    model = MESR(in_channels=1, mid_channels=32, out_channels=1, num_blocks=12)

    transform_lr = transforms.Compose([
        transforms.ToTensor(),
        # transforms.Lambda(lambda x: x / 255.0),  # Normalize to [0, 1]
        transforms.Normalize((0,), (1.0,))
    ])

    transform_hr = transforms.Compose([
        transforms.ToTensor(),
        # transforms.Lambda(lambda x: x / 255.0),  # Normalize to [0, 1]
        #transforms.Normalize((0.5,), (0.5,))
    ])

    # Load the dataset
    lr_dir = "/media/user/9c7eaef1-35fa-4210-889c-9e2b99342586/user/abul/RESM/sdo patches/dataset sdo patches low res"
    hr_dir = "/media/user/9c7eaef1-35fa-4210-889c-9e2b99342586/user/abul/RESM/sdo patches/dataset sdo patches"

    full_dataset = SuperResolutionDataset(
        lr_dir=lr_dir,
        hr_dir=hr_dir,
        lr_transform=transform_lr,
        hr_transform=transform_hr
    )


    # Splitting the dataset
    train_size = int(0.8 * len(full_dataset))
    val_size = len(full_dataset) - train_size

    train_dataset, val_dataset = random_split(full_dataset, [train_size, val_size])
    train_loader, val_loader = dataloaders(train_dataset, val_dataset, batch_size=32)

    model_summary(model, device)
    setup_training(model, device, train_loader, val_loader)

main()


CUDA is available!
Number of available GPUs: 1
Current device: 0
Device name: NVIDIA RTX A6000
----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Conv2d-1         [-1, 32, 128, 128]             320
            Conv2d-2         [-1, 64, 128, 128]          18,496
              SiLU-3         [-1, 64, 128, 128]               0
           Dropout-4         [-1, 64, 128, 128]               0
            Conv2d-5         [-1, 64, 128, 128]          36,928
              SiLU-6         [-1, 64, 128, 128]               0
           Dropout-7         [-1, 64, 128, 128]               0
            Conv2d-8         [-1, 32, 128, 128]          18,464
              SiLU-9         [-1, 32, 128, 128]               0
          Dropout-10         [-1, 32, 128, 128]               0
           Conv2d-11         [-1, 32, 128, 128]           1,056
AdaptiveAvgPool2d-12             [-1, 32, 1, 1]               0
        

/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetr

Validation Loss: 0.1037
Validation PSNR: 15.8344
Validation SSIM: 0.0919
Validation PCC: 0.3410
Validation RMSE: 0.1615
Time taken for epoch 1: 79.5419 sec
--------------------------------------------------
Epoch 2/500
Step 1/131, Charbonnier Loss: 0.1027, Pixel Loss: 0.1027, Combined Loss: 0.2055, Gradient Norm: 0.1196, Step time: 0.3439 sec
Step 2/131, Charbonnier Loss: 0.1043, Pixel Loss: 0.1043, Combined Loss: 0.2085, Gradient Norm: 0.1371, Step time: 0.3431 sec
Step 3/131, Charbonnier Loss: 0.1032, Pixel Loss: 0.1032, Combined Loss: 0.2063, Gradient Norm: 0.2975, Step time: 0.3407 sec
Step 4/131, Charbonnier Loss: 0.1050, Pixel Loss: 0.1050, Combined Loss: 0.2101, Gradient Norm: 0.1943, Step time: 0.3445 sec
Step 5/131, Charbonnier Loss: 0.1034, Pixel Loss: 0.1034, Combined Loss: 0.2067, Gradient Norm: 0.0501, Step time: 0.3429 sec
Step 6/131, Charbonnier Loss: 0.1047, Pixel Loss: 0.1047, Combined Loss: 0.2095, Gradient Norm: 0.2483, Step time: 0.3420 sec
Step 7/131, Charbonnier L

/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetr

Validation Loss: 0.1018
Validation PSNR: 15.9524
Validation SSIM: 0.0947
Validation PCC: 0.3572
Validation RMSE: 0.1594
Time taken for epoch 2: 79.3947 sec
--------------------------------------------------
Epoch 3/500
Step 1/131, Charbonnier Loss: 0.1017, Pixel Loss: 0.1017, Combined Loss: 0.2035, Gradient Norm: 0.0539, Step time: 0.3433 sec
Step 2/131, Charbonnier Loss: 0.1021, Pixel Loss: 0.1021, Combined Loss: 0.2041, Gradient Norm: 0.0387, Step time: 0.3427 sec
Step 3/131, Charbonnier Loss: 0.1017, Pixel Loss: 0.1017, Combined Loss: 0.2035, Gradient Norm: 0.0869, Step time: 0.3429 sec
Step 4/131, Charbonnier Loss: 0.1011, Pixel Loss: 0.1011, Combined Loss: 0.2022, Gradient Norm: 0.0247, Step time: 0.3440 sec
Step 5/131, Charbonnier Loss: 0.1013, Pixel Loss: 0.1013, Combined Loss: 0.2027, Gradient Norm: 0.0890, Step time: 0.3428 sec
Step 6/131, Charbonnier Loss: 0.1022, Pixel Loss: 0.1022, Combined Loss: 0.2045, Gradient Norm: 0.0272, Step time: 0.3430 sec
Step 7/131, Charbonnier L

...

Validation Loss: 0.0563
Validation PSNR: 23.1348
Validation SSIM: 0.4160
Validation PCC: 0.8233
Validation RMSE: 0.0697
Time taken for epoch 197: 79.3410 sec
--------------------------------------------------
Epoch 198/500
Step 1/131, Charbonnier Loss: 0.0556, Pixel Loss: 0.0556, Combined Loss: 0.1113, Gradient Norm: 0.0132, Step time: 0.3459 sec
Step 2/131, Charbonnier Loss: 0.0563, Pixel Loss: 0.0563, Combined Loss: 0.1125, Gradient Norm: 0.0018, Step time: 0.3485 sec
Step 3/131, Charbonnier Loss: 0.0573, Pixel Loss: 0.0573, Combined Loss: 0.1145, Gradient Norm: 0.0030, Step time: 0.3489 sec
Step 4/131, Charbonnier Loss: 0.0561, Pixel Loss: 0.0561, Combined Loss: 0.1122, Gradient Norm: 0.0035, Step time: 0.3481 sec
Step 5/131, Charbonnier Loss: 0.0563, Pixel Loss: 0.0563, Combined Loss: 0.1126, Gradient Norm: 0.0059, Step time: 0.3488 sec
Step 6/131, Charbonnier Loss: 0.0560, Pixel Loss: 0.0560, Combined Loss: 0.1120, Gradient Norm: 0.0025, Step time: 0.3476 sec
Step 7/131, Charbonni

/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetr

Validation Loss: 0.0563
Validation PSNR: 23.1348
Validation SSIM: 0.4159
Validation PCC: 0.8233
Validation RMSE: 0.0697
Time taken for epoch 198: 79.5723 sec
--------------------------------------------------
Epoch 199/500
Step 1/131, Charbonnier Loss: 0.0563, Pixel Loss: 0.0563, Combined Loss: 0.1126, Gradient Norm: 0.0053, Step time: 0.3476 sec
Step 2/131, Charbonnier Loss: 0.0559, Pixel Loss: 0.0559, Combined Loss: 0.1119, Gradient Norm: 0.0029, Step time: 0.3479 sec
Step 3/131, Charbonnier Loss: 0.0561, Pixel Loss: 0.0561, Combined Loss: 0.1121, Gradient Norm: 0.0049, Step time: 0.3472 sec
Step 4/131, Charbonnier Loss: 0.0565, Pixel Loss: 0.0565, Combined Loss: 0.1130, Gradient Norm: 0.0058, Step time: 0.3492 sec
Step 5/131, Charbonnier Loss: 0.0559, Pixel Loss: 0.0559, Combined Loss: 0.1118, Gradient Norm: 0.0019, Step time: 0.3484 sec
Step 6/131, Charbonnier Loss: 0.0559, Pixel Loss: 0.0559, Combined Loss: 0.1118, Gradient Norm: 0.0045, Step time: 0.3480 sec
Step 7/131, Charbonni

/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetrics/utilities/prints.py:70: FutureWarning: Importing `spectral_angle_mapper` from `torchmetrics.functional` was deprecated and will be removed in 2.0. Import `spectral_angle_mapper` from `torchmetrics.image` instead.
  _future_warning(
/home/user/miniforge3/envs/pytorch/lib/python3.10/site-packages/torchmetr

Validation Loss: 0.0563
Validation PSNR: 23.1348
Validation SSIM: 0.4160
Validation PCC: 0.8233
Validation RMSE: 0.0697
Time taken for epoch 199: 79.6998 sec
--------------------------------------------------
Epoch 200/500
Step 1/131, Charbonnier Loss: 0.0565, Pixel Loss: 0.0565, Combined Loss: 0.1131, Gradient Norm: 0.0045, Step time: 0.3485 sec
Step 2/131, Charbonnier Loss: 0.0561, Pixel Loss: 0.0561, Combined Loss: 0.1122, Gradient Norm: 0.0019, Step time: 0.3473 sec
Step 3/131, Charbonnier Loss: 0.0564, Pixel Loss: 0.0564, Combined Loss: 0.1128, Gradient Norm: 0.0034, Step time: 0.3481 sec
Step 4/131, Charbonnier Loss: 0.0562, Pixel Loss: 0.0562, Combined Loss: 0.1124, Gradient Norm: 0.0019, Step time: 0.3472 sec
Step 5/131, Charbonnier Loss: 0.0563, Pixel Loss: 0.0563, Combined Loss: 0.1127, Gradient Norm: 0.0029, Step time: 0.3491 sec
Step 6/131, Charbonnier Loss: 0.0563, Pixel Loss: 0.0563, Combined Loss: 0.1125, Gradient Norm: 0.0038, Step time: 0.3474 sec
Step 7/131, Charbonni

Testing

In [ ]:
model = MESR(in_channels=1, mid_channels=32, out_channels=1, num_blocks=12).to(device)
model.load_state_dict(torch.load("model_output/Mar07_2137/model_weight_epoch30.pth"))
# model.eval()


In [ ]:
from predict import prediction
import matplotlib.pyplot as plt
import numpy as np

transform = transforms.Compose([
    transforms.ToTensor(),
    # transforms.Normalize(mean=[0.5], std=[0.5])
    transforms.Lambda(lambda x: x * 255.0),
])

def prediction(model, image_path):
    model.eval()
    image = Image.open(image_path).convert('L')
    image = transform(image).unsqueeze(0).to(device)
    with torch.inference_mode():
        output = model(image)
    return output.squeeze(0).cpu()


In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from PIL import Image
import torchvision.transforms as transforms
import cv2

# Example usage with visualization
low_res_image_path = '/media/user/9c7eaef1-35fa-4210-889c-9e2b99342586/user/abul/RESM NEW NEW/RESM/20100903_0025_hr_patch_11.jpg'  # Replace with your low-res image path
hr_image_path = '/media/user/9c7eaef1-35fa-4210-889c-9e2b99342586/user/abul/RESM/sdo patches/dataset sdo patches/20100903_0025_hr_patch_11.jpg'  # Replace with your high-res image path

# Get SRCNN/MESR enhanced image
predicted_image_tensor = prediction(model, low_res_image_path)
predicted_image_pil = transforms.ToPILImage()(predicted_image_tensor)  # Convert tensor to PIL image
predicted_image_np = np.array(predicted_image_pil)  # Convert PIL to NumPy array

# Load low-resolution image
low_res_pil = Image.open(low_res_image_path).convert('L')
low_res_np = np.array(low_res_pil)

# Load ground truth high-resolution image
hr_pil = Image.open(hr_image_path).convert('L')
hr_np = np.array(hr_pil)

# Perform bicubic interpolation
bicubic_np = cv2.resize(low_res_np, (predicted_image_np.shape[1], predicted_image_np.shape[0]), interpolation=cv2.INTER_CUBIC)

# Visualization using matplotlib
plt.figure(figsize=(24, 6))  # Adjust figure size as needed

# Subplot 1: Low-Resolution Image
plt.subplot(1, 4, 1)
plt.imshow(low_res_np, cmap='gray')
plt.title('Low-Resolution')
plt.axis('off')

# Subplot 2: Bicubic Interpolation Image
plt.subplot(1, 4, 2)
plt.imshow(bicubic_np, cmap='gray')
plt.title('Bicubic Interpolation')
plt.axis('off')

# Subplot 3: MESR Enhanced Image
plt.subplot(1, 4, 3)
plt.imshow(predicted_image_np, cmap='gray')
plt.title('MESR Enhanced')
plt.axis('off')

# Subplot 4: Ground Truth (High-Resolution) Image
plt.subplot(1, 4, 4)
plt.imshow(hr_np, cmap='gray')
plt.title('Ground Truth')
plt.axis('off')

plt.tight_layout()
plt.show()

# Optionally save the images
predicted_image_pil.save('path_to_save_predicted_image.png')
bicubic_pil = Image.fromarray(bicubic_np)
bicubic_pil.save('path_to_save_bicubic_image.png')
hr_pil.save('path_to_save_hr_image.png')


In [ ]:
predicted_image_tensor